In [16]:
print("ok")

ok


In [167]:
from langchain import PromptTemplate
from langchain.chains import RetrievalQA
from langchain.embeddings import HuggingFaceEmbeddings
from langchain.vectorstores import Pinecone
import pinecone
from langchain.document_loaders import PyPDFLoader, DirectoryLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.prompts import PromptTemplate
from langchain.llms import CTransformers
from pinecone import Pinecone, ServerlessSpec

#langchain==0.0.225

In [42]:
import os
from dotenv import load_dotenv
load_dotenv()  # take env variable from .env

Pinecone_API_KEY_=os.getenv("Pinecone_API_KEY")
Pinecone_API_env_= os.getenv("Pinecone_API_env")
#print(key)
print(Pinecone_API_env_)

us-east-1


In [19]:
#Extract data from the PDF
def load_pdf(data):
    loader = DirectoryLoader(data,
                    glob="*.pdf",
                    loader_cls=PyPDFLoader)
    
    documents = loader.load()

    return documents

In [20]:
extracted_data = load_pdf("../data")

In [14]:
!pip install pypdf

In [33]:
# extracted_data[0].metadata
len(extracted_data)  #loading 637 pages in the list

637

In [29]:
#create text chunks
def text_split(extracted_data):
    text_splitter = RecursiveCharacterTextSplitter(chunk_size = 500, chunk_overlap = 20)
    text_chunks = text_splitter.split_documents(extracted_data)

    return text_chunks

In [30]:
text_chunks = text_split(extracted_data)
print("length of my chunk:", len(text_chunks))

length of my chunk: 7020


In [59]:
text_chunks[50].page_content

'Joseph Knight, P.A.\nMedical WriterWinton, CA\nMelissa Knopper\nMedical WriterChicago, IL\nKaren Krajewski, M.S., C.G.C.\nGenetic CounselorAssistant Professor of NeurologyWayne State UniversityDetroit, MI\nJeanne Krob, M.D., F.A.C.S.\nPhysician, writerPittsburgh, PA\nJennifer Lamb\nMedical WriterSpokane, WA\nRichard H. Lampert\nSenior Medical EditorW.B. Saunders Co.Philadelphia, PA\nJeffrey P. Larson, R.P.T.\nPhysical TherapistSabin, MN\nJill Lasker\nMedical WriterMidlothian, V A\nKristy Layman'

In [34]:
#download embedding model
def download_hugging_face_embeddings():
    embeddings = HuggingFaceEmbeddings(model_name="sentence-transformers/all-MiniLM-L6-v2")
    return embeddings

In [35]:
embeddings = download_hugging_face_embeddings()

c:\Users\kevin\OneDrive\Documents\Learning\Youtube\GenAI\Chatbot_Project\GenAI_Charbot1\mchatbot\lib\site-packages\huggingface_hub\utils\_deprecation.py:131: FutureWarning: 'cached_download' (from 'huggingface_hub.file_download') is deprecated and will be removed from version '0.26'. Use `hf_hub_download` instead.
  warnings.warn(warning_message, FutureWarning)
c:\Users\kevin\OneDrive\Documents\Learning\Youtube\GenAI\Chatbot_Project\GenAI_Charbot1\mchatbot\lib\site-packages\transformers\tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


In [36]:
embeddings

HuggingFaceEmbeddings(client=SentenceTransformer(
  (0): Transformer({'max_seq_length': 256, 'do_lower_case': False}) with Transformer model: BertModel 
  (1): Pooling({'word_embedding_dimension': 384, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False})
  (2): Normalize()
), model_name='sentence-transformers/all-MiniLM-L6-v2', cache_folder=None, model_kwargs={}, encode_kwargs={})

In [57]:
#query_result = embeddings.embed_query("Hello world")
query_result1 = embeddings.embed_query(text_chunks[3].page_content)
print("Length", len(query_result1))

Length 384


In [40]:
query_result[0:10]

[-0.03447728976607323,
 0.03102322667837143,
 0.006735010538250208,
 0.026108987629413605,
 -0.03936200588941574,
 -0.16030244529247284,
 0.06692402064800262,
 -0.0064414627850055695,
 -0.047450508922338486,
 0.01475893147289753]

In [43]:

#Initializing the Pinecone
pinecone.init(api_key=Pinecone_API_KEY_,
              environment=Pinecone_API_env_)

index_name="med-chatbot"

#Creating Embeddings for Each of The Text Chunks & storing
docsearch=Pinecone.from_texts([t.page_content for t in text_chunks], embeddings, index_name=index_name)

AttributeError: init is no longer a top-level attribute of the pinecone package.

Please create an instance of the Pinecone class instead.

Example:

    import os
    from pinecone import Pinecone, ServerlessSpec

    pc = Pinecone(
        api_key=os.environ.get("PINECONE_API_KEY")
    )

    # Now do stuff
    if 'my_index' not in pc.list_indexes().names():
        pc.create_index(
            name='my_index', 
            dimension=1536, 
            metric='euclidean',
            spec=ServerlessSpec(
                cloud='aws',
                region='us-west-2'
            )
        )



In [60]:
text_chunks1=[t.page_content for t in text_chunks]

In [65]:
model = SentenceTransformer('sentence-transformers/all-MiniLM-L6-v2')
embeddings1 = model.encode(text_chunks1)

c:\Users\kevin\OneDrive\Documents\Learning\Youtube\GenAI\Chatbot_Project\GenAI_Charbot1\mchatbot\lib\site-packages\transformers\tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


In [71]:
# len(embeddings1)
# (embeddings1[0])
embeddings1

array([[ 0.0017461 , -0.03350284, -0.03290391, ..., -0.0055564 ,
         0.10660911,  0.05099718],
       [ 0.00292344, -0.01455028, -0.03022254, ...,  0.00513137,
         0.09235159,  0.04713925],
       [ 0.01135415, -0.0445466 , -0.00519446, ..., -0.03019343,
        -0.00275956,  0.04715074],
       ...,
       [ 0.01451089, -0.00133084, -0.00749073, ..., -0.04619954,
         0.00073319,  0.09123775],
       [ 0.03931931,  0.01020944, -0.02842464, ..., -0.01608236,
        -0.04819496,  0.10338915],
       [ 0.05632068,  0.012677  , -0.0285632 , ..., -0.00335932,
        -0.02053688,  0.11145322]], dtype=float32)

In [83]:
# creating index
from pinecone import Pinecone, ServerlessSpec
pc = Pinecone(api_key=Pinecone_API_KEY_)
index_name = "med-chatbot"

if index_name not in pc.list_indexes().names():
    pc.create_index(
        name=index_name,
        dimension=384,
        metric="cosine",
        spec=ServerlessSpec(
            cloud='aws',
            region='us-east-1'
        )
    )
index = pc.Index(index_name)
index.describe_index_stats()


{'dimension': 384,
 'index_fullness': 0.0,
 'namespaces': {},
 'total_vector_count': 0}

In [78]:
# creating vectors to upload
vectors = []
i=1
for d, e in zip(text_chunks1, embeddings1):
    vectors.append({
        "id": str(i),
        "values": e,
        "metadata": {'text': d}
    })
    i=i+1

vectors

[{'id': '1',
  'values': array([ 1.74609746e-03, -3.35028432e-02, -3.29039060e-02,  7.16807740e-03,
         -1.46031911e-02,  1.02618514e-02, -1.15153240e-02,  2.29302183e-01,
         -2.32323650e-02,  4.12047748e-03, -3.65608633e-02,  8.59210938e-02,
          1.29721826e-02,  5.22179045e-02, -1.02326170e-01, -3.13898223e-03,
         -1.26869148e-02,  4.71849518e-04, -2.84858383e-02, -5.02591580e-02,
          1.15510020e-02,  7.78064504e-02,  9.28282812e-02, -1.37972971e-02,
         -1.69350505e-02, -2.59558987e-02, -4.95650545e-02, -4.61312607e-02,
          7.29051931e-03, -1.35531919e-02,  3.84394638e-02,  6.28047213e-02,
          1.83538124e-02,  8.24283902e-03,  1.71561202e-03, -3.98618467e-02,
         -1.16386712e-02,  1.64462551e-02,  2.55955644e-02,  9.10460651e-02,
          2.96727382e-02, -5.41602597e-02, -4.57656570e-02, -1.38538303e-02,
          2.57735141e-02,  1.03231035e-02, -5.36308698e-02,  2.12215744e-02,
          1.70277879e-02,  1.16122216e-01, -6.9631710

In [84]:
vectors[5]

{'id': '6',
 'values': [-0.005056883208453655,
  0.04913090541958809,
  -0.04827355593442917,
  0.07336482405662537,
  0.004527209792286158,
  0.012238314375281334,
  -0.026310469955205917,
  -0.005213037133216858,
  0.05958113446831703,
  -0.029366929084062576,
  0.10747119784355164,
  -0.040049705654382706,
  0.0502094067633152,
  -0.058578260242938995,
  -0.054277870804071426,
  -0.041375670582056046,
  -0.005753810983151197,
  0.03109920583665371,
  -0.039890583604574203,
  0.006015763618052006,
  -0.025515412911772728,
  -0.015900906175374985,
  -0.07473644614219666,
  0.023733094334602356,
  0.06816178560256958,
  -0.01837298832833767,
  -0.13871362805366516,
  -0.04481823742389679,
  0.05499321594834328,
  -0.09119535982608795,
  0.06329558789730072,
  0.12256185710430145,
  0.08980467915534973,
  0.052529435604810715,
  0.07832644879817963,
  0.018691053614020348,
  -0.013918546959757805,
  -0.036428987979888916,
  -0.09474652260541916,
  0.053312741219997406,
  0.0236259531229

In [86]:
#uploading the vector

index.upsert(
    vectors=vectors,
    namespace="ns1",
    batch_size=1000
)


Upserted vectors: 100%|██████████| 7020/7020 [02:20<00:00, 49.93it/s]


{'upserted_count': 7020}

In [87]:
index.describe_index_stats()

{'dimension': 384,
 'index_fullness': 0.0,
 'namespaces': {'ns1': {'vector_count': 7020}},
 'total_vector_count': 7020}

In [103]:
#If we already have an index we can load it like this
docsearch=Pinecone.from_existing_index(index_name, embeddings)

query = "What are Allergies"

docs=docsearch.similarity_search(query, k=3)

print("Result", docs)

AttributeError: type object 'Pinecone' has no attribute 'from_existing_index'

In [89]:
#querying from the vector db

query = "What are Allergies"

query_embedding = model.encode(query).tolist()
print(query_embedding)

results = index.query(
    namespace="ns1",
    vector=query_embedding,
    top_k=3,
    include_values=False,
    include_metadata=True
)

print(results)

[0.018147893249988556, -0.0077622090466320515, 0.016550738364458084, -0.02258744090795517, 0.08301927149295807, 0.0421304777264595, 0.04739130288362503, 0.009959189221262932, -0.03739221766591072, 0.07155657559633255, 0.0373200885951519, -0.062287475913763046, 0.017921365797519684, 0.01487043034285307, -0.03633667528629303, 0.08066535741090775, -0.03342956677079201, -0.04579087719321251, -0.0021369222085922956, -0.05767635628581047, -0.014061146415770054, 0.0995464026927948, -0.008254271931946278, -0.005863542668521404, -0.05176490172743797, 0.0695711001753807, -0.037493996322155, -0.09890780597925186, -0.055883828550577164, -0.03587562218308449, -0.04290857911109924, -0.0230269618332386, 0.002322745742276311, 0.056762635707855225, -0.04027225822210312, 0.0024839516263455153, -0.08057361096143723, 0.020133910700678825, 0.021937420591711998, 0.007606528699398041, -0.026822220534086227, 0.023933088406920433, -0.06894034892320633, -0.0370841883122921, -0.07588563859462738, 0.0623272880911

In [98]:
(results.matches)

[{'id': '1373',
  'metadata': {'text': 'GALE ENCYCLOPEDIA OF MEDICINE 2 117Allergies\n'
                       'Allergic rhinitis is commonly triggered by\n'
                       'exposure to household dust, animal fur,or pollen. The '
                       'foreign substance thattriggers an allergic reaction is '
                       'calledan allergen.\n'
                       'The presence of an allergen causes the\n'
                       "body's lymphocytes to begin producingIgE antibodies. "
                       'The lymphocytes of an allergy sufferer produce an '
                       'unusuallylarge amount of IgE.\n'
                       'IgE molecules attach to mast\n'
                       'cells, which contain histamine.HistaminePollen grains\n'
                       'Lymphocyte\n'
                       'FIRST EXPOSURE'},
  'score': 0.682538748,
  'values': []},
 {'id': '1356',
  'metadata': {'text': 'allergens are the following:\n'
                       '• p

In [99]:
## llm

## Complete llm implementation in trial2.ipynb

In [169]:
prompt_template="""
Use the following pieces of information to answer the user's question.
If you don't know the answer, just say that you don't know, don't try to make up an answer.

Context: {context}
Question: {question}

Only return the helpful answer below and nothing else.
Helpful answer:
"""
PROMPT=PromptTemplate(template=prompt_template, input_variables=["context", "question"])
chain_type_kwargs={"prompt": PROMPT}
llm=CTransformers(model="../model/llama-2-7b-chat.ggmlv3.q4_0.bin",
                  model_type="llama",
                  config={'max_new_tokens':512,
                          'temperature':0.8})


In [102]:
qa=RetrievalQA.from_chain_type(
    llm=llm, 
    chain_type="stuff", 
    retriever=docsearch.as_retriever(search_kwargs={'k': 2}),
    return_source_documents=True, 
    chain_type_kwargs=chain_type_kwargs)

NameError: name 'docsearch' is not defined

In [104]:
from langchain.vectorstores import Pinecone

text_field = "text"

# switch back to normal index for langchain
# index = pc.Index(index_name)

vectorstore = Pinecone(
    index, embeddings.embed_query, text_field
)

In [106]:
vectorstore

In [110]:
query1 = "What are Allergies?"

vectorstore.similarity_search(
    # query1,  # our search query
    query1,
    k=3  # return 3 most relevant docs
)

ValueError: The argument order for `query()` has changed; please use keyword arguments instead of positional arguments. Example: index.query(vector=[0.1, 0.2, 0.3], top_k=10, namespace='my_namespace')

In [145]:
vectorstore = pinecone.from_existing_index(index_name=index_name, embedding=embeddings,namespace="ns1")
retriever = vectorstore.as_retriever()

AttributeError: module 'pinecone' has no attribute 'from_existing_index'

# Correct code

In [162]:
 from langchain_pinecone import PineconeVectorStore

vectorstore = PineconeVectorStore(index_name=index_name, embedding=embeddings,namespace="ns1")


In [163]:
query1 = "What are acne?"

vectorstore.similarity_search(
    # query1,  # our search query
    query1,
    k=3  # return 3 most relevant docs
)

[Document(page_content='Acidosis seeRespiratory acidosis; Renal\ntubular acidosis; Metabolic acidosis\nAcne\nDefinition\nAcne is a common skin disease characterized by\npimples on the face, chest, and back. It occurs when thepores of the skin become clogged with oil, dead skincells, and bacteria.\nDescription\nAcne vulgaris, the medical term for common acne, is'),
 Document(page_content='GALE ENCYCLOPEDIA OF MEDICINE 2 25Acne\nAcne vulgaris affecting a woman’s face. Acne is the general\nname given to a skin disorder in which the sebaceousglands become inflamed. (Photograph by Biophoto Associ-\nates, Photo Researchers, Inc. Reproduced by permission.)GEM - 0001 to 0432 - A  10/22/03 1:41 PM  Page 25'),
 Document(page_content='ent purposes. For example, lotions, soaps, gels, andcreams containing benzoyl peroxide or tretinoin may beused to clear up mild to moderately severe acne.Isotretinoin (Accutane) is prescribed only for verysevere, disfiguring acne.\nAcne is a skin condition that occu

In [171]:
import langchain
print(langchain.__version__)

0.0.225


In [165]:
# Initialize a LangChain object for retrieving information from Pinecone.
knowledge = PineconeVectorStore.from_existing_index(
    index_name=index_name,
    namespace="ns1",
    embedding=embeddings
)

In [170]:
# Initialize a LangChain object for chatting with the LLM
# with knowledge from Pinecone. 
from langchain.chains import RetrievalQA 
qa = RetrievalQA.from_chain_type(
    llm=llm,
    chain_type="stuff",
    retriever=knowledge.as_retriever(),
    return_source_documents=True, 
    chain_type_kwargs=chain_type_kwargs
)

ValidationError: 1 validation error for RetrievalQA
retriever
  Can't instantiate abstract class BaseRetriever with abstract methods _aget_relevant_documents, _get_relevant_documents (type=type_error)

In [136]:
retriever = vectorstore.as_retriever(search_kwargs={'k': 2})

In [148]:
qa=RetrievalQA.from_chain_type(
    llm=llm, 
    chain_type="stuff", 
    retriever=retriever,
    return_source_documents=True, 
    chain_type_kwargs=chain_type_kwargs)

ValidationError: 1 validation error for RetrievalQA
retriever
  Can't instantiate abstract class BaseRetriever with abstract methods _aget_relevant_documents, _get_relevant_documents (type=type_error)